In [1]:
from bs4 import BeautifulSoup as bs
from pyparsing import line_end
from selenium import webdriver
from selenium.webdriver.chrome.service import Service as ChromeService
from webdriver_manager.chrome import ChromeDriverManager

from selenium.common.exceptions import NoSuchElementException


from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC

import requests
import time
from bs4 import BeautifulSoup

In [2]:
import pymysql

conn = pymysql.connect(host='127.0.0.1', user='play', passwd='123', database='sk17', port=3306)
cur = conn.cursor()

In [3]:
cur.execute("SELECT * from used_cars_id_ecar")

176658

In [4]:
ids = cur.fetchall()

In [5]:
url = "https://fem.encar.com/cars/detail/{}?pageid=dc_carsearch&listAdvType=normal&carid=39078057&view_type=hs_ad&adv_attribute=hs_ad&wtClick_korList=019&advClickPosition=kor_normal_p1_g1&tempht_arg=1f3VE7Elg2J9_0"

In [6]:
url = "https://fem.encar.com/cars/detail/{}"

In [7]:
def wait_return_text (loc, driver):
    try:
        return WebDriverWait(driver, 1).until(EC.presence_of_element_located((By.CSS_SELECTOR, loc))).text
    except:
        return ""

In [14]:
col = ['차량번호', '차대번호', '주행거리', '연식', '연료', '차종', '색상', '연비', '판매자이름', '판매링크', '모델명', '가격', '판매자ID']
data = []
failed_id = []

In [15]:
len(ids)

176658

In [16]:
n = 0


In [17]:
driver = webdriver.Chrome(service=ChromeService(ChromeDriverManager().install()))
for i in range(len(ids)):
    try:
        id = ids[i][0]
        row = [''] * 13
        driver.get(url.format(id))

        WebDriverWait(driver, 10).until(EC.element_to_be_clickable((By.CSS_SELECTOR, "#wrap > div > div.Layout_contents__MD95o > div.ResponsiveLayout_wrap__XLqcM > div.ResponsiveLayout_content_area__yyYYv > div:nth-child(1) > div > button"))).click()
        #car_num
        row[0] = wait_return_text("#bottom_sheet > div.BottomSheet-module_bottom_sheet__LeljN.BottomSheet-module_pc_position__3fgGY > div.BottomSheet-module_inner_contents__-vTmf > div > ul > li:nth-child(1) > span", driver)

        #car_vin
        row[1] = ""

        #car_distance
        row[2] = wait_return_text("#bottom_sheet > div.BottomSheet-module_bottom_sheet__LeljN.BottomSheet-module_pc_position__3fgGY > div.BottomSheet-module_inner_contents__-vTmf > div > ul > li:nth-child(3) > span", driver)

        #car_year
        row[3] = wait_return_text("#bottom_sheet > div.BottomSheet-module_bottom_sheet__LeljN.BottomSheet-module_pc_position__3fgGY > div.BottomSheet-module_inner_contents__-vTmf > div > ul > li:nth-child(2) > span", driver)

        #car_fuel_type
        row[4] = wait_return_text("#bottom_sheet > div.BottomSheet-module_bottom_sheet__LeljN.BottomSheet-module_pc_position__3fgGY > div.BottomSheet-module_inner_contents__-vTmf > div > ul > li:nth-child(5) > span", driver)

        #car_type
        row[5] = wait_return_text("#bottom_sheet > div.BottomSheet-module_bottom_sheet__LeljN.BottomSheet-module_pc_position__3fgGY > div.BottomSheet-module_inner_contents__-vTmf > div > ul > li:nth-child(7) > span", driver)

        #car_color
        row[6] = wait_return_text("#bottom_sheet > div.BottomSheet-module_bottom_sheet__LeljN.BottomSheet-module_pc_position__3fgGY > div.BottomSheet-module_inner_contents__-vTmf > div > ul > li:nth-child(8) > span", driver)

        #car_fuel_effi
        row[7] = ""

        #car_link
        row[9] = url.format(id)
        WebDriverWait(driver, 3).until(EC.element_to_be_clickable((By.CSS_SELECTOR, "#bottom_sheet > div.BottomSheet-module_bottom_sheet__LeljN.BottomSheet-module_pc_position__3fgGY > button > svg > path"))).click()

        html = driver.page_source
        soup = bs(html, 'lxml')

        #car_model
        if soup.find('h3', class_='DetailSummary_tit_car__0OEVh') :
            row[10] = soup.find('h3', class_='DetailSummary_tit_car__0OEVh').find('span').text

        #seller_name
        row[8] = soup.find('strong', class_='DetailSeller_name__e6P5f').text if soup.find('strong', class_='DetailSeller_name__e6P5f') else None
        #car_price
        row[11] = soup.find('span', class_='DetailLeadCase_point__vdG4b').text if soup.find('span', class_='DetailLeadCase_point__vdG4b') else None

        #셀러id
        if soup.find('ul', class_='DetailSeller_info_seller__suhjh'):
            lis = soup.find('ul', class_='DetailSeller_info_seller__suhjh').find_all('li')
            if len(lis) >= 3:
                row[12] = soup.find('ul', class_='DetailSeller_info_seller__suhjh').find_all('li')[2].text

        data.append(row)
        print()
        print("번호 :", i, 'row : ',row)
    except Exception as e:
        failed_id.append(ids[i])
        continue


번호 : 0 row :  ['86어4035', '', '45,437km', '09년 11월 (10년형)', '디젤', '카고(화물)트럭', '청색', '', '손현빈', 'https://fem.encar.com/cars/detail/18526213', '포터 Ⅱ', '800', '인천 서구 염곡로 149']

번호 : 1 row :  ['76러4536', '', '41,769km', '04년 05월', '디젤', '버스', '흰색 (아이보리)', '', '손현빈', 'https://fem.encar.com/cars/detail/18536458', '카운티', '1,750', '인천 서구 염곡로 149']

번호 : 2 row :  ['89어9831', '', '499,172km', '09년 11월 (10년형)', '디젤', '윙바디/탑', '흰색', '', '이한수', 'https://fem.encar.com/cars/detail/19941253', '노부스 중형트럭', '2,600', '경기 수원시 권선구 정조로 262']

번호 : 3 row :  ['20우7257', '', '146,000km', '10년 06월', '가솔린', '중형차', '검정색', '', '황인호', 'https://fem.encar.com/cars/detail/20163952', 'YF 쏘나타', '600', '']

번호 : 4 row :  ['86바4222', '', '465,953km', '10년 03월', '디젤', '윙바디/탑', '흰색', '', '이한수', 'https://fem.encar.com/cars/detail/20626812', '노부스 중형트럭', '2,900', '경기 수원시 권선구 정조로 262']

번호 : 5 row :  ['81노7666', '', '322,207km', '08년 03월 (09년형)', '디젤', '윙바디/탑', '흰색', '', '이한수', 'https://fem.encar.com/cars/detail/21588176', '노부스

KeyboardInterrupt: 

In [10]:
col_op = []
data_op = []

In [19]:
len(data)

18212

In [20]:
import pandas as pd

dataframe = pd.DataFrame(data=data, columns=col)

In [22]:
dataframe.to_csv('output2.csv', index=False, encoding='utf-8')

In [23]:
dataframe.to_csv('df_utf_sig.csv', index=False, encoding='utf-8-sig')

In [25]:
data2=[]
failed_id2 = []

In [26]:
driver = webdriver.Chrome(service=ChromeService(ChromeDriverManager().install()))
for i in range(18463, len(ids)):
    try:
        id = ids[i][0]
        row = [''] * 13
        driver.get(url.format(id))

        WebDriverWait(driver, 10).until(EC.element_to_be_clickable((By.CSS_SELECTOR, "#wrap > div > div.Layout_contents__MD95o > div.ResponsiveLayout_wrap__XLqcM > div.ResponsiveLayout_content_area__yyYYv > div:nth-child(1) > div > button"))).click()
        #car_num
        row[0] = wait_return_text("#bottom_sheet > div.BottomSheet-module_bottom_sheet__LeljN.BottomSheet-module_pc_position__3fgGY > div.BottomSheet-module_inner_contents__-vTmf > div > ul > li:nth-child(1) > span", driver)

        #car_vin
        row[1] = ""

        #car_distance
        row[2] = wait_return_text("#bottom_sheet > div.BottomSheet-module_bottom_sheet__LeljN.BottomSheet-module_pc_position__3fgGY > div.BottomSheet-module_inner_contents__-vTmf > div > ul > li:nth-child(3) > span", driver)

        #car_year
        row[3] = wait_return_text("#bottom_sheet > div.BottomSheet-module_bottom_sheet__LeljN.BottomSheet-module_pc_position__3fgGY > div.BottomSheet-module_inner_contents__-vTmf > div > ul > li:nth-child(2) > span", driver)

        #car_fuel_type
        row[4] = wait_return_text("#bottom_sheet > div.BottomSheet-module_bottom_sheet__LeljN.BottomSheet-module_pc_position__3fgGY > div.BottomSheet-module_inner_contents__-vTmf > div > ul > li:nth-child(5) > span", driver)

        #car_type
        row[5] = wait_return_text("#bottom_sheet > div.BottomSheet-module_bottom_sheet__LeljN.BottomSheet-module_pc_position__3fgGY > div.BottomSheet-module_inner_contents__-vTmf > div > ul > li:nth-child(7) > span", driver)

        #car_color
        row[6] = wait_return_text("#bottom_sheet > div.BottomSheet-module_bottom_sheet__LeljN.BottomSheet-module_pc_position__3fgGY > div.BottomSheet-module_inner_contents__-vTmf > div > ul > li:nth-child(8) > span", driver)

        #car_fuel_effi
        row[7] = ""

        #car_link
        row[9] = url.format(id)
        WebDriverWait(driver, 3).until(EC.element_to_be_clickable((By.CSS_SELECTOR, "#bottom_sheet > div.BottomSheet-module_bottom_sheet__LeljN.BottomSheet-module_pc_position__3fgGY > button > svg > path"))).click()

        html = driver.page_source
        soup = bs(html, 'lxml')

        #car_model
        if soup.find('h3', class_='DetailSummary_tit_car__0OEVh') :
            row[10] = soup.find('h3', class_='DetailSummary_tit_car__0OEVh').find('span').text

        #seller_name
        row[8] = soup.find('strong', class_='DetailSeller_name__e6P5f').text if soup.find('strong', class_='DetailSeller_name__e6P5f') else None
        #car_price
        row[11] = soup.find('span', class_='DetailLeadCase_point__vdG4b').text if soup.find('span', class_='DetailLeadCase_point__vdG4b') else None

        #셀러id
        if soup.find('ul', class_='DetailSeller_info_seller__suhjh'):
            lis = soup.find('ul', class_='DetailSeller_info_seller__suhjh').find_all('li')
            if len(lis) >= 3:
                row[12] = soup.find('ul', class_='DetailSeller_info_seller__suhjh').find_all('li')[2].text

        data2.append(row)
        print()
        print("번호 :", i, 'row : ',row)
    except Exception as e:
        failed_id2.append(ids[i])
        continue


번호 : 18463 row :  ['168로1207', '', '84,068km', '21년 04월', '가솔린', '경차', '흰색', '', '김용진', 'https://fem.encar.com/cars/detail/38722807', '더 뉴 레이', '1,079', '충남 천안시 동남구']

번호 : 18464 row :  ['241구3763', '', '13,981km', '24년 03월', '가솔린', '경차', '흰색', '', None, 'https://fem.encar.com/cars/detail/38722855', '더 뉴 모닝 (JA)', '1,390', '']

번호 : 18465 row :  ['63모2342', '', '109,854km', '17년 09월 (18년형)', '디젤', 'SUV', '검정색', '', '김주영', 'https://fem.encar.com/cars/detail/38722890', '더 뉴 쏘렌토', '1,640', '경기 수원시 권선구']

번호 : 18466 row :  ['85라8961', '', '1,056,293km', '15년 03월', '디젤', '윙바디/탑', '흰색', '', '김홍기', 'https://fem.encar.com/cars/detail/38722941', '메가트럭', '3,300', '충북 옥천군']

번호 : 18467 row :  ['07보5564', '', '138,230km', '18년 02월', '가솔린', '중형차', '흰색', '', '정명호', 'https://fem.encar.com/cars/detail/38722946', '스팅어', '1,290', '광주 서구 매월1로62번길 24']

번호 : 18468 row :  ['198더5067', '', '178,532km', '18년 03월', 'LPG(일반인 구입)LPG 자세히보기', '중형차', '흰색', '', '박상억', 'https://fem.encar.com/cars/detail/38722948', 

KeyboardInterrupt: 

In [ ]:
# 22400 까지함

In [27]:
len(data2)

3883

In [28]:
import pandas as pd

dataframe2 = pd.DataFrame(data=data2, columns=col)

In [30]:
dataframe2.to_csv('df_utf_sig2.csv', index=False, encoding='utf-8-sig')